In [9]:
from selenium import webdriver
from selenium.webdriver.edge.service import Service
from selenium.webdriver.edge.options import Options
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
import time

# Đường dẫn tới file msedgedriver.exe
PATH = 'edgedriver_win64/msedgedriver.exe'

# Tạo đối tượng Service với đường dẫn EdgeDriver
service = Service(PATH)

# Tạo đối tượng Options (nếu cần tùy chỉnh thêm cài đặt)
options = Options()

# Khởi tạo WebDriver với Service và Options
driver = webdriver.Edge(service=service, options=options)

# Mở trang Facebook
driver.get("https://www.facebook.com/")
driver.maximize_window()

In [3]:
# Tìm và nhập email và mật khẩu
username = driver.find_element(By.ID, 'email')
password = driver.find_element(By.ID, 'pass')

username.send_keys('#')  # Thay your_email bằng email của bạn
password.send_keys('#')  # Thay your_password bằng mật khẩu của bạn

# Submit form đăng nhập
password.send_keys(Keys.RETURN)


In [5]:
# Điều hướng đến trang danh sách bạn bè
driver.get('#')

In [ ]:
import pandas as pd
from selenium.common.exceptions import StaleElementReferenceException, NoSuchElementException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import time
import re
import json
import os

# Hàm để lấy danh sách bạn chung của một người bạn
def get_mutual():
    mutual_friends = set()
    last_height = driver.execute_script("return document.body.scrollHeight")
    
    while True:
        try:
            friends_elements = WebDriverWait(driver, 10).until(
                EC.presence_of_all_elements_located((By.XPATH, "//div[@class='x1iyjqo2 x1pi30zi']"))
            )
            for f in friends_elements:
                mutual_friends.add(f.text)
        except StaleElementReferenceException:
            continue  # Quay lại đầu vòng lặp nếu có lỗi

        driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
        time.sleep(5)

        new_height = driver.execute_script("return document.body.scrollHeight")
        if new_height == last_height: 
            break
        last_height = new_height
    
    return mutual_friends

# Khởi tạo tập hợp để lưu tên bạn bè, liên kết profile đã được xử lý và danh sách thông tin bạn bè
friends = set()
friends_data = []
profile_links_processed = set()

# Tạo hoặc đọc file JSON
json_file_path = 'friends_info.json'
if os.path.exists(json_file_path):
    with open(json_file_path, 'r', encoding='utf-8') as json_file:
        friends_data = json.load(json_file)
        # Lưu vào tập hợp để kiểm tra nhanh
        friends = {friend['name'] for friend in friends_data}
else:
    with open(json_file_path, 'w', encoding='utf-8') as json_file:
        json.dump([], json_file)

def process_mutual_friends(mutual_friends):
    processed_friends = []
    for friend in mutual_friends:
        # Sử dụng biểu thức chính quy để loại bỏ số lượng bạn chung và văn bản " bạn chung"
        name = re.sub(r'\d+ bạn chung', '', friend).strip()
        if name:
            processed_friends.append(name)  # Thêm tên vào danh sách
    return ", ".join(processed_friends)  # Nối tất cả các tên bằng dấu phẩy và khoảng trắng

def process_name_friends(friend_names):
    processed_friends = []
    name_part = friend_names.split('\n')[0]
    # Sử dụng biểu thức chính quy để loại bỏ số lượng bạn chung và văn bản " bạn chung"
    name = re.sub(r'\d+ bạn chung', '', name_part).strip()
    if name:
        processed_friends.append(name)  # Thêm tên vào danh sách
    
    return ", ".join(processed_friends)  

# Bắt đầu thu thập dữ liệu bạn bè
while len(friends_data) < 110:
    current_scroll_position = driver.execute_script("return window.scrollY;")
    try:
        # Lấy lại danh sách bạn bè
        friends_elements = WebDriverWait(driver, 10).until(
            EC.presence_of_all_elements_located((By.XPATH, "//div[@class='x1iyjqo2 x1pi30zi']"))
        )
        for index, f in enumerate(friends_elements):
            friend_name = f.text
            friend_name_fix = process_name_friends(friend_name)

            # Kiểm tra xem bạn đã tồn tại trong file JSON chưa
            if friend_name_fix in friends:
                print(f"{friend_name_fix} đã tồn tại, bỏ qua.")
                continue  # Nếu bạn đã tồn tại, bỏ qua vòng lặp hiện tại

            friends.add(friend_name_fix)
            friend_info = {"name": friend_name_fix}
            
            try:
                profile_link_element = f.find_element(By.XPATH, ".//a[@href and not(contains(@href, 'friends_mutual'))]")
                profile_href = profile_link_element.get_attribute('href')

                # Kiểm tra xem link profile có trùng không
                if profile_href not in profile_links_processed:
                    profile_links_processed.add(profile_href)
                    friend_info["profile_link"] = profile_href

                    # Mở trang profile để lấy thông tin bạn chung
                    profile_link_element.click()
                    time.sleep(5)  # Đợi trang tải
                    try:
                        list_friends_link = WebDriverWait(driver, 10).until(
                            EC.presence_of_element_located((By.XPATH, "//a[contains(@href, 'friends') and .//span[text()='Bạn bè']]"))
                        )
                        list_friends_link.click()
                        time.sleep(5)
                        try:
                            driver.execute_script("window.scrollBy(0, 100);")  # Cuộn xuống một khoảng nhỏ
                            mutuals_friends_link = WebDriverWait(driver, 10).until(
                                EC.presence_of_element_located((By.XPATH, "//a[contains(@href, 'friends_mutual') and .//span[text()='Bạn chung']]"))
                            )
                            mutuals_friends_link.click()
                            time.sleep(5)
                            mutual_friends = get_mutual()
                            friend_info["mutual_friends"] = process_mutual_friends(mutual_friends)
                            friend_info["mutual_count"] = len(mutual_friends)
                            driver.back()
                            time.sleep(5)  # Chỉ lưu tên bạn chung
                        except NoSuchElementException:
                            print(f"Không tìm thấy liên kết 'Bạn chung' cho {friend_name_fix}")
                            continue
                    except NoSuchElementException:
                        print(f"Không tìm thấy liên kết 'Bạn bè' cho {friend_name_fix}")
                        continue
                    try:
                        driver.refresh()
                        info_friends_link = WebDriverWait(driver, 10).until(
                            EC.presence_of_element_located((By.XPATH, "//a[contains(@href, 'about') and .//span[contains(text(), 'Giới thiệu')]]"))
                        )
                        info_friends_link.click()
                        time.sleep(5)
                        try:
                            info_basic_friends_link = WebDriverWait(driver, 10).until(
                                EC.presence_of_element_located((By.XPATH, "//a[contains(@href, 'about') and .//span[contains(text(), 'Thông tin liên hệ và cơ bản')]]"))
                            )
                            info_basic_friends_link.click()
                            time.sleep(5)
                            # Tìm tất cả các phần tử với lớp 'xu06os2 x1ok221b' chứa các span
                            elements = driver.find_elements(By.XPATH, "//div[contains(@class, 'xu06os2') and contains(@class, 'x1ok221b')]//span")
                            
                            # Khởi tạo mảng để lưu trữ các giá trị duy nhất
                            unique_texts = []
                            
                            for element in elements:
                                text = element.text.strip()
                                if text not in [''] and text not in unique_texts:
                                    unique_texts.append(text)
                            
                            # Xử lý các giá trị duy nhất
                            if 'Di động' in unique_texts:
                                index = unique_texts.index('Di động') - 1 
                                friend_info['Phone'] = unique_texts[index]
                            else:
                                friend_info["Phone"] = "Không có Phone"
                            if 'Email' in unique_texts:
                                index = unique_texts.index('Email') - 1 
                                friend_info['Email'] = unique_texts[index]
                            else:
                                friend_info["Email"] = "Không có Email"
                            if 'Instagram' in unique_texts:
                                index = unique_texts.index('Instagram') - 1 
                                friend_info['Instagram'] = unique_texts[index]
                            else:
                                friend_info["Instagram"] = "Không có Instagram"
                            if 'Threads' in unique_texts:
                                index = unique_texts.index('Threads') - 1 
                                friend_info['Threads'] = unique_texts[index]
                            else:
                                friend_info["Threads"] = "Không có Threads"
                            if 'Giới tính' in unique_texts:
                                index = unique_texts.index('Giới tính') - 1 
                                friend_info['Giới tính'] = unique_texts[index]
                            else:
                                friend_info["Giới tính"] = "Không có Giới tính"
                            if 'Ngày sinh' in unique_texts:
                                index = unique_texts.index('Ngày sinh') - 1 
                                friend_info['Ngày sinh'] = unique_texts[index]
                            else:
                                friend_info["Ngày sinh"] = "Không có Ngày sinh"
                            if 'Năm sinh' in unique_texts:
                                index = unique_texts.index('Năm sinh') - 1 
                                friend_info['Năm sinh'] = unique_texts[index]
                            else:
                                friend_info["Năm sinh"] = "Không có Năm sinh"
                            print(friend_info)

                            # Kiểm tra xem bạn đã có trong file chưa
                            existing_friend = next((friend for friend in friends_data if friend['name'] == friend_info['name']), None)
                            if existing_friend:
                                print(f"{friend_info['name']} đã tồn tại trong file.")
                                continue  # Bỏ qua người bạn này nếu đã tồn tại

                            friends_data.append(friend_info)
                            # Cập nhật file JSON
                            with open(json_file_path, 'w', encoding='utf-8') as json_file:
                                json.dump(friends_data, json_file, ensure_ascii=False, indent=4)
                            driver.back()
                            time.sleep(5)
                            driver.back()
                            time.sleep(5)
                        except NoSuchElementException:
                            print(f"Không tìm thấy liên kết 'Thông tin liên hệ và cơ bản' cho {friend_name_fix}")
                            continue
                    except NoSuchElementException:
                        print(f"Không tìm thấy liên kết 'Giới thiệu' cho {friend_name_fix}")
                        continue
            except NoSuchElementException:
                print(f"Không tìm thấy liên kết profile cho {friend_name_fix}")
    except Exception as e:
        print(f"Có lỗi xảy ra: {e}")
        driver.execute_script("window.scrollTo(0, arguments[0]);", current_scroll_position)
    if len(friends_data) < 110:
            # Cuộn xuống một khoảng nhỏ để tải thêm bạn bè
            driver.execute_script("window.scrollBy(0, 100);")
            time.sleep(3)
print("Hoàn thành thu thập thông tin bạn bè!")


Chỉ Xích Thiên Nhai đã tồn tại, bỏ qua.
Tran Phụng đã tồn tại, bỏ qua.
Jun Nguyễn đã tồn tại, bỏ qua.
Kiến Minh đã tồn tại, bỏ qua.
Anh Mai đã tồn tại, bỏ qua.
Trần Quốc Hoàng đã tồn tại, bỏ qua.
Khôi Lê đã tồn tại, bỏ qua.
Nguyễn Quí đã tồn tại, bỏ qua.
Tài Đức đã tồn tại, bỏ qua.
Minh Khôi đã tồn tại, bỏ qua.
Thái Tuấn đã tồn tại, bỏ qua.
Hiền Nghĩa đã tồn tại, bỏ qua.
Nguyễn Anh Nghị đã tồn tại, bỏ qua.
Hải Hậu Mai đã tồn tại, bỏ qua.
Hoàng Danh đã tồn tại, bỏ qua.
Nguyễn Quí đã tồn tại, bỏ qua.
Nhân đã tồn tại, bỏ qua.
Tú Châu đã tồn tại, bỏ qua.
Lê Huyền đã tồn tại, bỏ qua.
Nguyễn Ngọc Quốc Trung đã tồn tại, bỏ qua.
Xuân Quang đã tồn tại, bỏ qua.
Hà Khang Trần đã tồn tại, bỏ qua.
Tran Thanh Phong đã tồn tại, bỏ qua.
Lê Tấn Phát đã tồn tại, bỏ qua.
Ngọc Thảo đã tồn tại, bỏ qua.
Huygia Lam đã tồn tại, bỏ qua.
Tài Châu đã tồn tại, bỏ qua.
Đức Kiên đã tồn tại, bỏ qua.
Trần Nhân đã tồn tại, bỏ qua.
Huy Le đã tồn tại, bỏ qua.
Thanh Tuấn đã tồn tại, bỏ qua.
Khánh Thi đã tồn tại, bỏ qua.


In [19]:
from neo4j import GraphDatabase
import json

# Kết nối với Neo4j
uri = "bolt://localhost:7687"
username = "neo4j"
password = "02062003"
driver = GraphDatabase.driver(uri, auth=(username, password))

# Tải file JSON từ hệ thống
file_path = 'friends_info.json'
with open(file_path, 'r', encoding='utf-8') as f:
    data = json.load(f)

def create_person_and_relationships(tx, person):
    # Tạo node cho người dùng chính
    tx.run("""
        MERGE (p:Person {name: $name})
        SET p.profile_link = $profile_link,
            p.mutual_count = $mutual_count,
            p.Phone = $Phone,
            p.Email = $Email,
            p.Instagram = $Instagram,
            p.Threads = $Threads,
            p.Gender = $Gender,
            p.BirthDate = $BirthDate,
            p.BirthYear = $BirthYear
    """, 
    name=person['name'],
    profile_link=person['profile_link'],
    mutual_count=person['mutual_count'],
    Phone=person.get('Phone', 'Không có Phone'),
    Email=person.get('Email', 'Không có Email'),
    Instagram=person.get('Instagram', 'Không có Instagram'),
    Threads=person.get('Threads', 'Không có Threads'),
    Gender=person.get('Giới tính', 'Không có Giới tính'),
    BirthDate=person.get('Ngày sinh', 'Không có Ngày sinh'),
    BirthYear=person.get('Năm sinh', 'Không có Năm sinh'))

    # Tạo mối quan hệ mutual_friends cho từng người bạn
    if 'mutual_friends' in person and person['mutual_friends']:
        mutual_friends = person['mutual_friends'].split(', ')
        for friend in mutual_friends:
            # Tạo quan hệ MUTUAL_FRIEND giữa người dùng chính và bạn chung
            tx.run("""
                MATCH (p:Person {name: $name}), (f:Person {name: $friend})
                MERGE (p)-[:MUTUAL_FRIEND]->(f)
            """, friend=friend, name=person['name'])

# Thêm dữ liệu vào Neo4j
with driver.session() as session:
    for person in data:
        session.write_transaction(create_person_and_relationships, person)

# Đóng kết nối
driver.close()

C:\Users\Administrator\AppData\Local\Temp\ipykernel_13916\3845127801.py:53: DeprecationWarning: write_transaction has been renamed to execute_write
  session.write_transaction(create_person_and_relationships, person)
